<h1 align=center>Model Training</h1>

<h3>Install Packages</h3>

In [1]:
!pip install ultralytics --quiet
!pip install "ray[tune]" --quiet
!pip install -U ipywidgets --quiet

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
bigframes 0.22.0 requires google-cloud-bigquery[bqstorage,pandas]>=3.10.0, but you have google-cloud-bigquery 2.34.4 which is incompatible.
bigframes 0.22.0 requires google-cloud-storage>=2.0.0, but you have google-cloud-storage 1.44.0 which is incompatible.
bigframes 0.22.0 requires pandas<2.1.4,>=1.5.0, but you have pandas 2.2.2 which is incompatible.
dataproc-jupyter-plugin 0.1.79 requires pydantic~=1.10.0, but you have pydantic 2.9.2 which is incompatible.


<h3>Imports</h3>

In [2]:
import os
import shutil
from distutils.dir_util import copy_tree

from kaggle_secrets import UserSecretsClient

from ultralytics.data.utils import autosplit
from ultralytics import YOLO
from ultralytics import settings

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


<h3>Hyperparameters</h3>

In [3]:
# HYPERPARAMETERS
# Data Split
TRAIN_FRACTION = 0.8
VAL_FRACTION = 0.1
TEST_FRACTION = 0.1
EPOCHS = 250
TRACKER = 'wandb'

AUTOTUNE = True

assert ((TRAIN_FRACTION + VAL_FRACTION + TEST_FRACTION) == 1.0), "Sum of split fraction != 1"

<h3>Setup Trackers</h3>

In [4]:
if TRACKER == 'wandb':
    !pip install -U wandb
    import wandb
    
    user_secrets = UserSecretsClient()
    wandb_auth_token = user_secrets.get_secret("WANDB_AUTH_TOKEN")
    
    wandb.login(key=wandb_auth_token)

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.0/16.0 MB 80.6 MB/s eta 0:00:00
  Attempting uninstall: wandb
    Found existing installation: wandb 0.18.3
    Uninstalling wandb-0.18.3:
      Successfully uninstalled wandb-0.18.3


wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.
wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [5]:
if TRACKER == 'mlflow':
    !pip install mlflow --quiet
    !pip install pyngrok --quiet
    
    import mlflow
    from pyngrok import ngrok
    from getpass import getpass
    
    get_ipython().system_raw("mlflow ui --port 5000 --backend-store-uri runs/mlflow &")

    # Terminate open tunnels if exist
    ngrok.kill()

    user_secrets = UserSecretsClient()
    ngrok_auth_token = user_secrets.get_secret("NGROK_AUTH_TOKEN")
    ngrok.set_auth_token(ngrok_auth_token)

    # Open an HTTPs tunnel on port 5000 for http://localhost:5000
    ngrok_tunnel = ngrok.connect(addr="5000", proto="http", bind_tls=True)
    print("MLflow Tracking UI:", ngrok_tunnel.public_url)

    # Update a setting
    settings.update({"mlflow": True})

<h3>Dataset Preparation</h3>

In [6]:
# Copy train images from kaggle input directory to kaggle output directory
dataset_source_dir = '/kaggle/input/fixed-wing-uavs/dataset-07-10-2024/'
dataset_target_dir = '/kaggle/working/dataset/'

data_yaml_source_path = '/kaggle/working/dataset/data_kaggle.yaml'
data_yaml_target_path = '/kaggle/working/data_kaggle.yaml'

os.makedirs(dataset_target_dir, exist_ok=True)
copy_tree(dataset_source_dir, dataset_target_dir)
shutil.move(data_yaml_source_path, data_yaml_target_path)

'/kaggle/working/data_kaggle.yaml'

In [7]:
# create data split
autosplit(path="/kaggle/working/dataset", weights = (TRAIN_FRACTION, VAL_FRACTION, TEST_FRACTION))

Autosplitting images from /kaggle/working/dataset


100%|██████████| 891/891 [00:00<00:00, 19456.19it/s]


<h3>Model Training</h3>

In [8]:
# use pre-trained yolov11 model
model = YOLO("yolo11n.pt")

if AUTOTUNE == True:
    import os
    os.environ['RAY_CHDIR_TO_TRIAL_DIR'] = '0'
    from ray import tune
    param_space = {
                    # 'optimizer': tune.choice(['SGD', 'Adam', 'AdamW', 'NAdam', 'RAdam', 'RMSProp']),
                   "lr0": tune.loguniform(1e-5, 1e-1),
                   "lrf": tune.loguniform(0.01, 1.0),  # final OneCycleLR learning rate (lr0 * lrf)
                   "momentum": tune.loguniform(0.9, 0.999),  # SGD momentum/Adam beta1
                   "weight_decay": tune.uniform(0.0, 0.001),  # optimizer weight decay 5e-4
                   "warmup_epochs": tune.uniform(0.0, 5.0),  # warmup epochs (fractions ok)
                   "warmup_momentum": tune.uniform(0.0, 0.95),  # warmup initial momentum
                   "box": tune.uniform(0.02, 0.2),  # box loss gain
                   "cls": tune.uniform(0.2, 4.0),  # cls loss gain (scale with pixels)
                   }
    
    results = model.tune(data="/kaggle/working/data_kaggle.yaml",
                         use_ray=True,
                         space=param_space,
                         epochs=EPOCHS,
                         gpu_per_trial=1,
                         project='key-parameters-tune-dataset-v1',
                         save=True)
else:
    results = model.train(data="/kaggle/working/data_kaggle.yaml",
                          epochs=15,
                          project='fixed-wing-uavs',
                          name='trial')

2024-10-25 09:40:51,324	INFO wandb.py:318 -- Already logged into W&B.
(_WandbLoggingActor pid=402) wandb: Currently logged in as: amit-hershkovitz (amit-hershkovitz-technion-israel-institute-of-technology). Use `wandb login --relogin` to force relogin
(_WandbLoggingActor pid=402) wandb: Tracking run with wandb version 0.18.5
(_WandbLoggingActor pid=402) wandb: Run data is saved locally in /tmp/ray/session_2024-10-25_09-40-38_447439_24/artifacts/2024-10-25_09-40-43/_tune_2024-10-25_09-40-43/driver_artifacts/_tune_34795_00000_0_box=0.1495,cls=3.9619,lr0=0.0001,lrf=0.6869,momentum=0.9868,warmup_epochs=4.1220,warmup_momentum=0.8148,weight_2024-10-25_09-40-51/wandb/run-20241025_094056-34795_00000
(_WandbLoggingActor pid=402) wandb: Run `wandb offline` to turn off syncing.
(_WandbLoggingActor pid=402) wandb: Syncing run _tune_34795_00000
(_WandbLoggingActor pid=402) wandb: ⭐️ View project at https://wandb.ai/amit-hershkovitz-technion-israel-institute-of-technology/YOLOv8-tune
(_WandbLoggingA

(_tune pid=370) Ultralytics 8.3.22 🚀 Python-3.10.14 torch-2.4.0 CUDA:0 (Tesla P100-PCIE-16GB, 16269MiB)
(_tune pid=370) engine/trainer: task=detect, mode=train, model=yolo11n.pt, data=/kaggle/working/data_kaggle.yaml, epochs=250, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=key-parameters-tune-dataset-v1, name=train, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_co

  0%|          | 0.00/755k [00:00<?, ?B/s]
100%|██████████| 755k/755k [00:00<00:00, 4.57MB/s]


(_tune pid=370) Overriding model.yaml nc=80 with nc=1
(_tune pid=370) 
(_tune pid=370)                    from  n    params  module                                       arguments                     
(_tune pid=370)   0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
(_tune pid=370)   1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
(_tune pid=370)   2                  -1  1      6640  ultralytics.nn.modules.block.C3k2            [32, 64, 1, False, 0.25]      
(_tune pid=370)   3                  -1  1     36992  ultralytics.nn.modules.conv.Conv             [64, 64, 3, 2]                
(_tune pid=370)   4                  -1  1     26080  ultralytics.nn.modules.block.C3k2            [64, 128, 1, False, 0.25]     
(_tune pid=370)   5                  -1  1    147712  ultralytics.nn.modules.conv.Conv             [128, 128, 3, 2]              
(_tune pid=370)   6

(_tune pid=370) wandb: Currently logged in as: amit-hershkovitz (amit-hershkovitz-technion-israel-institute-of-technology). Use `wandb login --relogin` to force relogin
(_tune pid=370) wandb: Tracking run with wandb version 0.18.5
(_tune pid=370) wandb: Run data is saved locally in /kaggle/working/wandb/run-20241025_094113-rtb1p9q6
(_tune pid=370) wandb: Run `wandb offline` to turn off syncing.
(_tune pid=370) wandb: Syncing run train
(_tune pid=370) wandb: ⭐️ View project at https://wandb.ai/amit-hershkovitz-technion-israel-institute-of-technology/key-parameters-tune-dataset-v1
(_tune pid=370) wandb: 🚀 View run at https://wandb.ai/amit-hershkovitz-technion-israel-institute-of-technology/key-parameters-tune-dataset-v1/runs/rtb1p9q6


...

                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 3/3 [00:00<00:00,  7.15it/s]


(_tune pid=3309) 
(_tune pid=3309)       Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


  0%|          | 0/46 [00:00<?, ?it/s]
     91/250      2.62G    0.01772      3.841      1.475         37        640:   2%|▏         | 1/46 [00:00<00:09,  4.80it/s]
     91/250      2.63G    0.01613      3.314      1.346         39        640:   4%|▍         | 2/46 [00:00<00:09,  4.84it/s]
     91/250      2.63G    0.01529      3.166      1.314         44        640:   7%|▋         | 3/46 [00:00<00:08,  4.93it/s]
     91/250      2.63G    0.01537      3.173      1.325         37        640:   9%|▊         | 4/46 [00:00<00:09,  4.56it/s]
     91/250      2.63G     0.0149      3.019      1.311         39        640:  11%|█         | 5/46 [00:01<00:08,  4.67it/s]
     91/250      2.63G    0.01502      3.051       1.31         44        640:  13%|█▎        | 6/46 [00:01<00:08,  4.80it/s]
     91/250      2.63G    0.01475      3.025        1.3         39        640:  15%|█▌        | 7/46 [00:01<00:08,  4.74it/s]
     91/250      2.63G    0.01462      2.987      1.301         32        640: 

(_tune pid=3309)                    all         78         82        0.8      0.695        0.7      0.446


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 3/3 [00:00<00:00,  6.72it/s]
2024-10-25 12:11:29,465	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/kaggle/working/runs/detect/tune/_tune_2024-10-25_09-40-43' in 0.0415s.
(_WandbLoggingActor pid=3341) wandb:                                                                                
2024-10-25 12:11:32,118	INFO tune.py:1041 -- Total run time: 9048.24 seconds (9038.10 seconds for the tuning loop).
(_WandbLoggingActor pid=3341) wandb: 
(_WandbLoggingActor pid=3341) wandb: Run history:
(_WandbLoggingActor pid=3341) wandb:                    epoch ▁▁▁▁▁▂▂▂▂▂▂▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▆▆▆▆▇▇▇▇▇▇▇▇██
(_WandbLoggingActor pid=3341) wandb: iterations_since_restore ▁▁▁▁▂▂▂▂▂▂▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▆▆▆▆▆▆▆▆▇▇▇▇▇▇█
(_WandbLoggingActor pid=3341) wandb:         metrics/mAP50(B) ▁▃▄▆▆▆▂▇▆▆▇▇▇▇██▇▇█▇██▇▇███████▆▆██▇████
(_WandbLoggingActor pid=3341) wandb:      metri

In [9]:
best_result = results.get_best_result(metric='metrics/mAP50-95(B)', mode='max')
print(best_result)

import pickle as p
with open(f'{best_result.path}/params.pkl', 'rb') as f:
    params = p.load(f)

print(params)

Result(
  metrics={'metrics/precision(B)': 0.9276957180830103, 'metrics/recall(B)': 0.7823666300998532, 'metrics/mAP50(B)': 0.836739625074389, 'metrics/mAP50-95(B)': 0.6360440048270617, 'fitness': 0.6561135668517946},
  path='/kaggle/working/runs/detect/tune/_tune_2024-10-25_09-40-43/_tune_34795_00003_3_box=0.0498,cls=1.1657,lr0=0.0001,lrf=0.1865,momentum=0.9766,warmup_epochs=4.7203,warmup_momentum=0.2322,weight_2024-10-25_09-40-51',
  filesystem='local',
  checkpoint=None
)
{'lr0': 6.584631284556103e-05, 'lrf': 0.1864657467056177, 'momentum': 0.9766246626065974, 'weight_decay': 0.0007555184644232179, 'warmup_epochs': 4.720271709970277, 'warmup_momentum': 0.23218668399911463, 'box': 0.049797951800586396, 'cls': 1.1657339531236954, 'data': '/kaggle/working/data_kaggle.yaml'}


In [10]:
#import random
#
#def generate_random_image_paths(num_paths):
#    with open("/kaggle/working/autosplit_test.txt", "r") as f:
#        data = f.read().replace('./', '/kaggle/working/').split('\n')
#        data = data[:-1]
#    
#    generated_paths = []
#    image_nums = random.sample(range(0, len(data)), num_paths)
#
#    for i in image_nums:
#        generated_paths.append(data[i])
#        
#    return generated_paths

In [11]:
#paths = generate_random_image_paths(60)
#print(paths)

In [12]:
#model = YOLO('/kaggle/working/runs/detect/different_split/weights/best.pt')
#
#for result in results:
#    result.show()  # display to screen   